In [1]:
using Plots; 
using NBInclude
include("../src/RayTracer.jl")
using LaTeXStrings
using NPZ

In [2]:
function circleShape(h, k, r)
    th = LinRange(0, 2*π, 500)
    h .+ r*sin.(th), k .+ r*cos.(th)
end

circleShape (generic function with 1 method)

In [5]:
# choose dispersion relation: 
Dispersion = "Free"; # "ColdP", "StrongB"
# these correspond to free space dispersion relation, cold palsma dispersion relation, or cold plasma in strong magnetic field

"Free"

In [6]:
if Dispersion == "Free"
    funcU = RayTracer.ωFree
elseif Dispersion == "ColdP"
    funcU = RayTracer.ωSimple
elseif Dispersion == "StrongB"
    funcU = RayTracer.ωNR_e
else
    print("Error....")
end
time = 0.0

MagnetoVars = [0.5, 1, 1.0e14, 10., [1.0, 1.0], time] # θm, ωPul, B0, rNS, gamma factors
θ = LinRange(0.001, π - 0.001 , 100)
ϕ = 0.0


Csurf = zeros(length(θ))
x0CS_f = zeros(length(θ), 3)
rL = 10 .^ LinRange(log10.(10), 4, 10000)
for i in 1:length(θ)
    x0CS = [rL .* sin.(θ[i]) .* cos.(ϕ) rL .* sin.(θ[i]) .* sin.(ϕ) rL .* cos.(θ[i])];
    ωpL = RayTracer.GJ_Model_ωp_vec(x0CS, time, MagnetoVars[1], MagnetoVars[2], MagnetoVars[3], MagnetoVars[4])
    cx_list = RayTracer.get_crossings(log10.(ωpL) .- log10.(1e-6))
    cross = RayTracer.apply(cx_list, rL)
    if length(cx_list.i1) != 0
        Csurf[i] = cross[1]
    else
        Csurf[i] = 10.0
    end
    x0CS_f[i,:] =[Csurf[i] .* sin.(θ[i]) .* cos.(ϕ) Csurf[i] .* sin.(θ[i]) .* sin.(ϕ) Csurf[i] .* cos.(θ[i])];
end


k_factor = 1e-5 
ln_t_start = -16
ln_t_end = log(1e-2)
ntimes = 1000
tt = exp.(LinRange(ln_t_start, ln_t_end, ntimes) )
ode_err = 1e-5 # 
NumerPass = [ln_t_start, ln_t_end, ode_err]

x0 = [Csurf .* sin.(θ).*cos.(ϕ) Csurf.*sin.(θ).*sin.(ϕ) Csurf.*cos.(θ)];  
ωpL = RayTracer.GJ_Model_ωp_vec(x0, time, MagnetoVars[1], MagnetoVars[2], MagnetoVars[3], MagnetoVars[4])
θdir = rand(length(θ)) .* π;
ϕdir = rand(length(θ)) .* 2π;
k0 = [k_factor .* ωpL .* cos.(ϕ) .* sin.(θ) k_factor .* ωpL .* sin.(ϕ) .* sin.(θ) k_factor .* ωpL .* cos.(θ)];
xfin, kfin = RayTracer.propagate(funcU, x0, k0, ntimes, MagnetoVars, NumerPass);
z_dir = xfin[:, 3, :];

θ = LinRange(-0.003, π+0.003, 100)
ϕ = π
Csurf = zeros(length(θ))
x0CS_f2 = zeros(length(θ), 3)
rL = 10 .^ LinRange(log10.(10), 4, 10000)
for i in 1:length(θ)
    x0CS = [rL .* sin.(θ[i]) .* cos.(ϕ) rL .* sin.(θ[i]) .* sin.(ϕ) rL .* cos.(θ[i])];
    ωpL = RayTracer.GJ_Model_ωp_vec(x0CS, time, MagnetoVars[1], MagnetoVars[2], MagnetoVars[3], MagnetoVars[4])
    cx_list = RayTracer.get_crossings(log10.(ωpL) .- log10.(1e-6))
    cross = RayTracer.apply(cx_list, rL)
    if length(cx_list.i1) != 0
        Csurf[i] = cross[1]
    else
        Csurf[i] = 10.0
    end
    x0CS_f2[i,:] =[Csurf[i] .* sin.(θ[i]) .* cos.(ϕ) Csurf[i] .* sin.(θ[i]) .* sin.(ϕ) Csurf[i] .* cos.(θ[i])];
end



x0 = [Csurf .* sin.(θ).*cos.(ϕ) Csurf.*sin.(θ).*sin.(ϕ) Csurf.*cos.(θ)];  
ωpL = RayTracer.GJ_Model_ωp_vec(x0, time, MagnetoVars[1], MagnetoVars[2], MagnetoVars[3], MagnetoVars[4])
θdir = rand(length(θ)) .* π;
ϕdir = rand(length(θ)) .* 2π;
k0 = [k_factor .* ωpL .* cos.(ϕ) .* sin.(θ) k_factor .* ωpL .* sin.(ϕ) .* sin.(θ) k_factor .* ωpL .* cos.(θ)];

xfin2, kfin2 = RayTracer.propagate(funcU, x0, k0, ntimes, MagnetoVars, NumerPass);
z_dir2 = xfin2[:, 3, :];

plot(framestyle=:box, palette=:default, fontfamily="serif-roman")
for i in 1:length(θ)
    plot!(xfin[i, 1, :], z_dir[i,:], legend=false, palette=:cmyk)
    plot!(xfin2[i, 1, :], z_dir2[i,:], legend=false, palette=:cmyk)
    plot!(x0CS_f[:, 1], x0CS_f[:, 3], lw=2, c=:black, xlims=[-200,200],ylims=[-200, 200], fill=:true, fillalpha=0.005, legend=false,ylabel="z   [km]", xlabel="ρ   [km]")
    plot!(x0CS_f2[:, 1], x0CS_f2[:, 3], lw=2, c=:black, xlims=[-200,200],ylims=[-200, 200], fill=:true, fillalpha=0.005, legend=false,ylabel="z   [km]", xlabel="x   [km]")
end
plot!(circleShape(0, 0, 10), seriestype=[:shape, ], lw = 0.5, c =:blue, linecolor=:blue,legend=false,fillalpha=0.2 )
plot!(size=(500,500), grid=false)